In [1]:
import os
import glob
import time
from datetime import timedelta, datetime
import numpy as np
import pandas as pd
import qgrid

from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)
import gezi

from projects.feed.rank.monitor.taurus import Taurus

In [2]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [3]:
last_days = 30
start_time = None
end_time = None
# start_time = 20191210
# end_time = 20191220
# abids = [8,15,16]
# abids = [16, 8]
# abids = [16]
# abids = [8, 15]
# abids = [15]
# abids = [8]
abids = [16]
abids = [11]

assert len(abids) < 2, 'FIXME only 1 abid is ok now, as natural_diff wrong currenlty TODO'
product = 'sgsapp'
# product = 'newmse'

diff_spans_ = {
    8: [20200313, 20200319],
#     12: [20190130, 20200205],
#     11: [20190130, 20200205],
    7: [20200325, 20200331],
    10: [20200325, 20200331],
    11: [20200325, 20200331],
    15: [20200325, 20200331],
    16: [20200325, 20200331],
    17: [20200325, 20200331],
    18: [20200325, 20200331],
}
diff_spans = {}
for abid in abids:
  diff_spans[abid] = diff_spans_[abid]

diff_spans = None

In [4]:
worker_daily = Taurus()
worker_daily.init(abids, last_days, 'daily', product=product,
                  diff_spans=diff_spans, start_time=start_time, end_time=end_time)
worker_daily.run()

# for name 1(tuwen,video,small_video,total) 2(quality,total) 3(recommend,relative,total)
def show_daily(name, use_diff=True, quality=False, field=None):
  worker_daily.show(name, quality, field, use_diff=False)

SELECT * FROM feed_abtest_video_type_common_daily 
                WHERE product = 'sgsapp'
                AND abtest in ('6','4','11','5') 
                AND date BETWEEN '20200811' AND '20200911'
                AND video_type in ('0', '1', '2', 'total')
          
/home/gezi/mine/pikachu/projects/feed/rank/monitor/taurus.py:169: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/home/gezi/mine/pikachu/projects/feed/rank/monitor/taurus.py:169: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

18.377020359039307


In [5]:
w = worker_daily
d = worker_daily.ratio2
d = d.sort_values('date', ascending=False)
# pd.set_option('precision', 5)  
names = ['dis_user', 'click_user', 'click', 'duration', 'refresh_times', 'read_files', 'ctr', 'read_ratio', 'dur1', 'dur2', 
         'doc_dur', 'finish_ratio', 'praise', 'favor', 'share']
# d2 = d[d.name!='small_video'].groupby(['name', 'data_obj', 'abtest']).head(6).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]
d2 = d.groupby(['name', 'data_obj', 'abtest']).head(7).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]

# qgrid.show_grid(d2)
# d.groupby(['name', 'data_obj', 'abtest']).head(1)

In [6]:
d_ = d2[d2.data_obj=='total_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [7]:
d_ = d2[d2.data_obj=='quality_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [8]:
d_ = d2[d2.data_obj=='total_relative']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [9]:
w.ratio2[w.ratio2.name=='video'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
719  20200910  0.012922    0.018282  0.006121  0.045013       0.004155   
695  20200909  0.016465    0.028427  0.007671  0.042253       0.015262   
671  20200908  0.012025    0.018847  0.000473  0.022707       0.005741   
647  20200907  0.005640   -0.010674 -0.037319  0.001765      -0.006710   
623  20200906  0.012203    0.011251 -0.029566  0.026329       0.022038   
599  20200905  0.010804    0.020212  0.011581  0.035484       0.026467   
575  20200904  0.006350   -0.000516 -0.040028 -0.004619       0.012401   
551  20200903  0.008934    0.014006  0.020450 -0.010240       0.033937   
527  20200902  0.007307    0.025253  0.035387  0.019157       0.029160   
503  20200901  0.015980    0.022601  0.012165  0.004022       0.033150   
479  20200831  0.010469    0.008181  0.040083  0.019537       0.026929   
455  20200830  0.012625    0.012396  0.033074  0.019037       0.013949   
434  20200829  0.015378    0.020605  0.035915  0.011613       0.022365   
380  20200826  0.012664    0.014751  0.009690  0.007545       0.017699   
356  20200825  0.012120    0.024856  0.030489  0.017350       0.036900   
332  20200824  0.008021    0.020002  0.043688  0.040275       0.013641   
308  20200823  0.011449    0.011888  0.043842  0.037421       0.029240   
284  20200822  0.006991    0.014488  0.043358  0.026665       0.009714   
260  20200821  0.009778    0.015543  0.035832  0.038104       0.024166   
236  20200820  0.010628    0.017037  0.023166  0.011969       0.010643   
212  20200819  0.010115    0.010181  0.033244  0.019897       0.015871   
188  20200818  0.009298    0.018717  0.031295  0.017047       0.008263   
164  20200817  0.015042    0.024817  0.030451  0.017184       0.019457   
140  20200816  0.014500    0.026894  0.035565  0.028156       0.016430   
116  20200815  0.008603    0.023872  0.045796  0.030559       0.009333   
92   20200814  0.004615    0.002459  0.013081  0.004133       0.004531   
68   20200813  0.014174    0.021183  0.027608  0.038852       0.015353   
44   20200812  0.010548    0.019460  0.024669  0.029217       0.019038   
20   20200811  0.012398    0.020102  0.006361  0.009813       0.009176   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
719   -0.006730 -0.003588    0.005270  0.031664  0.026305  0.038664   
695   -0.008627 -0.011030    0.011788  0.025399  0.013486  0.034296   
671   -0.011405 -0.015636    0.006731  0.010555  0.003799  0.022151   
647   -0.042711 -0.037148   -0.016222 -0.003836  0.012578  0.040587   
623   -0.041264 -0.041095   -0.000945  0.013951  0.014880  0.057519   
599    0.000767 -0.002476    0.009309  0.024416  0.014958  0.023605   
575   -0.046091 -0.031263   -0.006819 -0.010889 -0.004109  0.036919   
551    0.011413  0.004634    0.005047 -0.018996 -0.023958 -0.030177   
527    0.027880  0.017061    0.017828  0.011764 -0.005990 -0.015803   
503   -0.003769 -0.007628    0.006518 -0.011775 -0.018175 -0.008065   
479    0.029315  0.020194   -0.002269  0.008977  0.011252 -0.019754   
455    0.020241  0.023366   -0.000227  0.006371  0.006591 -0.013764   
434    0.020257  0.013324    0.005153 -0.003686 -0.008774 -0.023541   
380   -0.002920  0.000316    0.002060 -0.005032 -0.007072 -0.002197   
356    0.018167  0.009359    0.012596  0.005198 -0.007297 -0.012775   
332    0.035433  0.033660    0.011880  0.032064  0.019936 -0.003405   
308    0.032024  0.024917    0.000439  0.025681  0.025228 -0.006152   
284    0.036138  0.033163    0.007437  0.019551  0.011981 -0.016064   
260    0.025810  0.018877    0.005713  0.028058  0.022166  0.002135   
236    0.012386  0.014694    0.006340  0.001339 -0.004942 -0.011030   
212    0.022907  0.020821    0.000067  0.009703  0.009636 -0.012946   
188    0.021843  0.020959    0.009361  0.007694 -0.001694 -0.014030   
164    0.015195  0.019334    0.009633  0.002108 -0.007456 -0.012967   
140    0.020767  0.020260    0.012218  0.013463  0.001261 -0.007230   
116    0.0369

In [10]:
w.ratio2[w.ratio2.name=='video'][w.ratio2.data_obj=='quality_recommend'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
717  20200910  0.013057    0.016221  0.022549  0.038758       0.008872   
693  20200909  0.016361    0.026337  0.010336  0.032060       0.019932   
669  20200908  0.011746    0.018692  0.024548  0.040512       0.008802   
645  20200907  0.005262   -0.012624 -0.030876 -0.006139      -0.002582   
621  20200906  0.012167    0.008234  0.007820  0.016934       0.024371   
597  20200905  0.009692    0.016589  0.007914  0.025816       0.028996   
573  20200904  0.006678    0.002464 -0.018343  0.028282       0.014247   
549  20200903  0.008512    0.014570  0.024210  0.009306       0.037286   
525  20200902  0.006796    0.023597  0.016247 -0.001849       0.033097   
501  20200901  0.015961    0.023393  0.000799 -0.019897       0.035745   
477  20200831  0.011087    0.009866  0.030229 -0.004072       0.028677   
454  20200830  0.012584    0.014725  0.010300 -0.008394       0.017960   
432  20200829  0.015296    0.024080  0.024912  0.001756       0.024803   
412  20200828  0.013690    0.018936  0.016142  0.007000       0.025451   
398  20200827  0.008779    0.018406  0.015956  0.000968       0.025817   
378  20200826  0.012112    0.016620  0.004685 -0.017805       0.019030   
354  20200825  0.012291    0.024396  0.017845  0.029190       0.040047   
330  20200824  0.008182    0.018905  0.007670  0.015416       0.015357   
306  20200823  0.011584    0.011242  0.009051  0.001256       0.030001   
282  20200822  0.006350    0.011936  0.015711  0.015738       0.013316   
258  20200821  0.008461    0.012368 -0.000273  0.015147       0.026137   
234  20200820  0.010474    0.017999 -0.006903 -0.014190       0.012744   
210  20200819  0.010345    0.008198 -0.010089 -0.009927       0.018310   
186  20200818  0.009622    0.019341 -0.000193  0.003034       0.010498   
162  20200817  0.014454    0.022485  0.007300  0.005480       0.022755   
138  20200816  0.014679    0.024345  0.003726  0.002213       0.019805   
114  20200815  0.008613    0.026528  0.015922  0.003822       0.012366   
90   20200814  0.004618    0.003955 -0.009975 -0.009564       0.005156   
66   20200813  0.014548    0.023193 -0.001768  0.010008       0.015866   
42   20200812  0.010797    0.019924  0.003815  0.019812       0.018764   
18   20200811  0.012031    0.021889 -0.002913  0.006315       0.010209   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
717    0.009386  0.007643    0.003100  0.025345  0.022252  0.015833   
693   -0.005896 -0.010730    0.009837  0.015482  0.005615  0.021516   
669    0.012644  0.006940    0.006857  0.028405  0.021475  0.015649   
645   -0.035950 -0.037428   -0.017791 -0.011333  0.006585  0.025469   
621   -0.004298 -0.014897   -0.003888  0.004730  0.008652  0.009065   
597   -0.001737 -0.008246    0.006833  0.015982  0.009092  0.017677   
573   -0.024837 -0.023298   -0.004180  0.021474  0.025758  0.047500   
549    0.015579  0.003313    0.006026  0.000791 -0.005214 -0.014518   
525    0.009397 -0.006190    0.016697 -0.008574 -0.024852 -0.017775   
501   -0.014922 -0.026778    0.007315 -0.035292 -0.042298 -0.020678   
477    0.018949  0.006107   -0.001211 -0.014990 -0.013833 -0.033345   
454   -0.002221  0.000190    0.002116 -0.020673 -0.022733 -0.018473   
432    0.009469  0.006332    0.008657 -0.013324 -0.021766 -0.022591   
412    0.002426 -0.007820    0.005175 -0.006592 -0.011708 -0.008998   
398    0.007111  0.004047    0.009526 -0.007727 -0.017125 -0.014741   
378   -0.007332 -0.007457    0.004453 -0.029552 -0.033848 -0.022587   
354    0.005506 -0.005213    0.011971  0.016711  0.004633  0.011121   
330   -0.000508  0.002595    0.010630  0.007197 -0.003421  0.007705   
306   -0.002505 -0.008585   -0.000334 -0.010203 -0.009870 -0.007734   
282    0.009313  0.005883    0.005544  0.009326  0.003755 -0.000039   
258   -0.008654 -0.019998    0.003878  0.006635  0.002745  0.015419   
234   -0.017209 -0.018680    0.007447 -0.024401 -0.031625 -0.007445   
210   -

In [11]:
w.ratio2[w.ratio2.name=='video'][w.ratio2.data_obj=='quality_relative'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
718  20200910  0.012851    0.019839  0.003337  0.047143            0.0   
694  20200909  0.021467    0.027480  0.007649  0.044942            0.0   
670  20200908  0.017295    0.017006 -0.003973  0.018246            0.0   
646  20200907  0.001921   -0.012656 -0.039176  0.003443            0.0   
622  20200906  0.002561    0.012284 -0.035386  0.028034            0.0   
598  20200905  0.018727    0.016260  0.012233  0.037534            0.0   
574  20200904  0.000301   -0.012247 -0.043394 -0.012104            0.0   
550  20200903  0.001555    0.008504  0.020814 -0.014472            0.0   
526  20200902  0.015311    0.026213  0.039642  0.024533            0.0   
502  20200901  0.011590    0.016686  0.014877  0.010464            0.0   
478  20200831  0.008212    0.015804  0.041901  0.024728            0.0   
433  20200829  0.014662    0.032199  0.038005  0.014911            0.0   
379  20200826  0.008415    0.019655  0.009766  0.013663            0.0   
355  20200825  0.017166    0.024949  0.032307  0.013466            0.0   
331  20200824  0.015682    0.029908  0.050501  0.048053            0.0   
307  20200823  0.006880    0.014866  0.050274  0.048095            0.0   
283  20200822  0.006319    0.015563  0.048949  0.031018            0.0   
259  20200821  0.013391    0.025239  0.043678  0.045627            0.0   
235  20200820  0.012118    0.022556  0.028666  0.018769            0.0   
211  20200819  0.009924    0.009219  0.042237  0.029383            0.0   
187  20200818  0.007189    0.022090  0.036772  0.021833            0.0   
163  20200817  0.017087    0.019140  0.035628  0.021807            0.0   
139  20200816  0.016795    0.032191  0.040278  0.036430            0.0   
115  20200815  0.013033    0.023558  0.050472  0.039587            0.0   
91   20200814  0.003593    0.001576  0.016818  0.007513            0.0   
67   20200813  0.014803    0.029813  0.032782  0.048157            0.0   
43   20200812  0.010370    0.021287  0.028373  0.032653            0.0   
19   20200811  0.014953    0.017771  0.008007  0.011790            0.0   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
718   -0.009396 -0.003697    0.006896  0.033857  0.026814  0.043632   
694   -0.013482 -0.012531    0.005882  0.023035  0.017057  0.036998   
670   -0.020906 -0.021901   -0.000283  0.000937  0.001216  0.022198   
646   -0.040988 -0.033102   -0.014574  0.001536  0.016261  0.044327   
622   -0.037865 -0.033773    0.009700  0.025395  0.015530  0.065647   
598   -0.006401 -0.000735   -0.002416  0.018460  0.020916  0.024941   
574   -0.043699 -0.015616   -0.012551 -0.012427  0.000160  0.032710   
550    0.019204  0.009403    0.006969 -0.015982 -0.022818 -0.034728   
526    0.023986  0.023841    0.010747  0.009071 -0.001672 -0.014707   
502    0.003252  0.004490    0.005013 -0.001121 -0.006143 -0.004381   
478    0.033378  0.026746    0.007516  0.016334  0.008780 -0.016478   
433    0.022988  0.008056    0.017281  0.000238 -0.016708 -0.022385   
379    0.001321  0.002693    0.011143  0.005188 -0.005854  0.003843   
355    0.014925  0.011342    0.007653 -0.003608 -0.011177 -0.018276   
331    0.034357  0.031911    0.014008  0.031930  0.017638 -0.002498   
307    0.043098  0.030062    0.007934  0.040933  0.032739 -0.002082   
283    0.042329  0.035169    0.009177  0.024505  0.015197 -0.017129   
259    0.029877  0.029264    0.011698  0.031801  0.019867  0.001819   
235    0.016375  0.022876    0.010317  0.006619 -0.003641 -0.009679   
211    0.032025  0.030293   -0.000702  0.019298  0.020007 -0.012343   
187    0.029423  0.021447    0.014809  0.014573 -0.000362 -0.014642   
163    0.018252  0.020882    0.002016  0.004656  0.002612 -0.013402   
139    0.023098  0.020338    0.015140  0.019315  0.004135 -0.003735   
115    0.037083  0.028473    0.010424  0.026310  0.015756 -0.010510   
91     0.013203  0.004898   -0.002011  0.003916  0.006046 -0.009143   
67     0.017787 

In [12]:
w.ratio2[w.ratio2.name=='tuwen'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
713  20200910  0.013449    0.014297  0.014804  0.016390       0.012783   
689  20200909  0.015809    0.017419  0.031410  0.019414       0.018263   
665  20200908  0.012542    0.018029  0.041171  0.047832       0.025305   
641  20200907  0.005933    0.000823  0.021523  0.019620       0.014112   
617  20200906  0.012454    0.008215  0.031986  0.027370       0.029147   
593  20200905  0.009381    0.017751  0.018931  0.018769       0.001719   
569  20200904  0.006036   -0.000239 -0.012441  0.042908      -0.006420   
545  20200903  0.009355   -0.012548 -0.005211  0.028646      -0.009966   
521  20200902  0.007335    0.010162  0.004791  0.005626       0.002924   
497  20200901  0.016211    0.009839  0.011559  0.006802       0.012125   
473  20200831  0.010954    0.011038 -0.008108 -0.015044       0.009809   
450  20200830  0.012652    0.007698 -0.004156 -0.003265      -0.005887   
428  20200829  0.014933    0.004735  0.016213  0.013071       0.009097   
374  20200826  0.012422    0.011156  0.001975  0.002909       0.006170   
350  20200825  0.012749    0.011698  0.012248  0.017407       0.002244   
326  20200824  0.008134    0.015560 -0.005684  0.006431      -0.013365   
302  20200823  0.012563    0.003299  0.005353  0.015329       0.001953   
278  20200822  0.006768    0.005365 -0.002803  0.000918       0.000436   
254  20200821  0.008522    0.012219  0.009708  0.011710       0.013155   
230  20200820  0.010032    0.008572 -0.003859  0.005014       0.005093   
206  20200819  0.010771    0.006059  0.006275  0.016936       0.006047   
182  20200818  0.009898    0.004512  0.009127  0.029659      -0.002477   
158  20200817  0.014518    0.006464  0.013874  0.014135      -0.004699   
134  20200816  0.014712    0.013933  0.007037  0.007317       0.004930   
110  20200815  0.008684    0.006568  0.002921  0.013371       0.012851   
86   20200814  0.004553    0.003670  0.019150  0.014695       0.020862   
62   20200813  0.014637    0.019589  0.020560  0.024531       0.012311   
38   20200812  0.010526    0.002342  0.008005  0.016363       0.002682   
14   20200811  0.012027    0.011687  0.005663  0.012184       0.003052   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
713    0.001325  0.003492    0.000833  0.002895  0.002074  0.001569   
689    0.015344  0.012659    0.001583  0.003534  0.001946 -0.011644   
665    0.028273  0.019996    0.005412  0.034825  0.029264  0.006369   
641    0.015481  0.011784   -0.005084  0.013590  0.018752 -0.001864   
617    0.019244  0.004494   -0.004208  0.014722  0.019001 -0.004533   
593    0.009450  0.005979    0.008290  0.009293  0.000987 -0.000168   
569   -0.018376 -0.011163   -0.006236  0.036641  0.043097  0.056057   
545   -0.014429 -0.005668   -0.021698  0.019122  0.041727  0.034044   
521   -0.002520 -0.007865    0.002809 -0.001698 -0.004526  0.000809   
497   -0.004576 -0.007715   -0.006276 -0.009257 -0.003021 -0.004701   
473   -0.018852 -0.021382    0.000076 -0.025722 -0.025792 -0.007003   
450   -0.016615 -0.005524   -0.004900 -0.015724 -0.010884  0.000878   
428    0.001255  0.001691   -0.010052 -0.001853  0.008293 -0.003109   
374   -0.010325 -0.008958   -0.001252 -0.009402 -0.008155  0.000938   
350   -0.000502 -0.004407   -0.001048  0.004588  0.005636  0.005062   
326   -0.013712 -0.001385    0.007362 -0.001689 -0.009067  0.012240   
302   -0.007137 -0.005027   -0.009150  0.002728  0.011941  0.009839   
278   -0.009531 -0.005054   -0.001391 -0.005831 -0.004477  0.003663   
254    0.001177 -0.005616    0.003667  0.003163 -0.000512  0.001943   
230   -0.013774 -0.009936   -0.001445 -0.004965 -0.003523  0.008847   
206   -0.004503 -0.002525   -0.004670  0.006052  0.010785  0.010584   
182   -0.000766  0.008289   -0.005343  0.019573  0.025004  0.020351   
158   -0.000654  0.007662   -0.007942 -0.000383  0.007605  0.000234   
134   -0.007552 -0.002386   -0.000772 -0.007274 -0.006534  0.000288   
110   -0.0056

In [13]:
w.ratio2[w.ratio2.name=='total'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
707  20200910  0.012954    0.018253  0.008282  0.037079       0.009087   
683  20200909  0.015636    0.023005  0.013794  0.035682       0.016923   
659  20200908  0.012656    0.012545  0.009955  0.029989       0.017230   
635  20200907  0.006262    0.000622 -0.023386  0.006757       0.005820   
611  20200906  0.012514    0.004155 -0.015910  0.026706       0.026100   
587  20200905  0.010152    0.016976  0.013260  0.031029       0.011788   
563  20200904  0.006030    0.000052 -0.033970  0.008382       0.000907   
539  20200903  0.009698   -0.002579  0.015348  0.000527       0.007621   
515  20200902  0.007382    0.015610  0.028323  0.015512       0.013864   
491  20200901  0.016072    0.011474  0.011734  0.004689       0.020511   
467  20200831  0.010411    0.007669  0.029187  0.010269       0.016766   
445  20200830  0.012621    0.006971  0.025363  0.013380       0.002557   
422  20200829  0.015243    0.010335  0.031703  0.011939       0.014723   
406  20200828  0.014948    0.007041  0.040712  0.033861       0.020347   
390  20200827  0.008657    0.012066  0.038263  0.025218       0.009543   
368  20200826  0.012827    0.009460  0.008258  0.006290       0.011022   
344  20200825  0.012695    0.016314  0.026087  0.017333       0.016797   
320  20200824  0.007887    0.016236  0.032270  0.030267      -0.001710   
296  20200823  0.012002    0.006956  0.035509  0.031271       0.013375   
272  20200822  0.007312    0.005930  0.032515  0.019252       0.004243   
248  20200821  0.009719    0.012853  0.029633  0.030437       0.017343   
224  20200820  0.010250    0.012355  0.016584  0.009792       0.007687   
200  20200819  0.010590    0.008777  0.027519  0.019028       0.010204   
176  20200818  0.009284    0.006331  0.025828  0.020624       0.001971   
152  20200817  0.015202    0.015661  0.026551  0.016219       0.005451   
128  20200816  0.014774    0.016497  0.029735  0.022115       0.009753   
104  20200815  0.008724    0.012060  0.036876  0.025407       0.011678   
80   20200814  0.004358    0.003126  0.014607  0.007526       0.014293   
56   20200813  0.014036    0.014781  0.025746  0.034148       0.013391   
32   20200812  0.010357    0.008875  0.020864  0.025152       0.008888   
8    20200811  0.012278    0.014476  0.006610  0.010486       0.005472   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
707   -0.004625 -0.002154    0.005221  0.023804  0.018484  0.028549   
683   -0.001798 -0.004822    0.007264  0.019753  0.012415  0.021557   
659   -0.002661 -0.008282   -0.000123  0.017109  0.017226  0.019770   
635   -0.029461 -0.027979   -0.005611  0.000500  0.006122  0.030843   
611   -0.028081 -0.035049   -0.008273  0.014010  0.022445  0.043269   
587    0.003071  0.000043    0.006751  0.020665  0.013810  0.017524   
563   -0.039766 -0.028612   -0.005941  0.002341  0.008292  0.043864   
539    0.005595  0.007743   -0.012157 -0.009074  0.003140 -0.014665   
515    0.020791  0.013050    0.008172  0.008071 -0.000111 -0.012547   
491   -0.004281 -0.007293   -0.004535 -0.011207 -0.006715 -0.006976   
467    0.018588  0.012398   -0.002719 -0.000141  0.002563 -0.018392   
445    0.012614  0.019882   -0.005587  0.000774  0.006360 -0.011819   
422    0.016236  0.013155   -0.004838 -0.003242  0.001585 -0.019228   
406    0.025396  0.018471   -0.007791  0.018660  0.026661 -0.006576   
390    0.029404  0.027516    0.003359  0.016467  0.012996 -0.012582   
368   -0.004503 -0.001852   -0.003324 -0.006442 -0.003139 -0.002024   
344    0.013233  0.007352    0.003571  0.004596  0.001002 -0.008580   
320    0.024226  0.029627    0.008276  0.022246  0.013821 -0.002036   
296    0.023222  0.020803   -0.004989  0.019042  0.024141 -0.004094   
272    0.025026  0.026227   -0.001374  0.011852  0.013207 -0.012880   
248    0.019729  0.013989    0.003104  0.020523  0.017371  0.000757   
224    0.006254  0.009162    0.002084 -0.000442 -0.002510 -0.006783   
200    

In [14]:
w.df[w.df.name=='total'][w.df.data_obj=='total_total']

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



product_name      date   name     data_obj  abtest        id         dis  \
11        sgsapp  20200811  total  total_total      11  39992003  26074674.0   
35        sgsapp  20200812  total  total_total      11  40160969  26285336.0   
59        sgsapp  20200813  total  total_total      11  40329985  26065928.0   
83        sgsapp  20200814  total  total_total      11  40498429  25687272.0   
107       sgsapp  20200815  total  total_total      11  40668505  25918756.0   
131       sgsapp  20200816  total  total_total      11  40838771  26038634.0   
155       sgsapp  20200817  total  total_total      11  41009631  25278280.0   
179       sgsapp  20200818  total  total_total      11  41179577  25127742.0   
203       sgsapp  20200819  total  total_total      11  41349283  25446068.0   
227       sgsapp  20200820  total  total_total      11  41520427  25649120.0   
251       sgsapp  20200821  total  total_total      11  41693551  25253634.0   
275       sgsapp  20200822  total  total_total      11  41867451  24963854.0   
299       sgsapp  20200823  total  total_total      11  42040775  25456804.0   
323       sgsapp  20200824  total  total_total      11  42953155  24941784.0   
347       sgsapp  20200825  total  total_total      11  43172929  24444572.0   
371       sgsapp  20200826  total  total_total      11  43391953  25428764.0   
393       sgsapp  20200827  total  total_total      11  43599845  25272546.0   
409       sgsapp  20200828  total  total_total      11  43747823  25443208.0   
425       sgsapp  20200829  total  total_total      11  43914601  25550906.0   
448       sgsapp  20200830  total  total_total      11  44128877  25178320.0   
470       sgsapp  20200831  total  total_total      11  44341169  23870548.0   
494       sgsapp  20200901  total  total_total      11  44562747  22708618.0   
518       sgsapp  20200902  total  total_total      11  44784443  22814082.0   
542       sgsapp  20200903  total  total_total      11  45006293  22848520.0   
566       sgsapp  20200904  total  total_total      11  45228115  22678198.0   
590       sgsapp  20200905  total  total_total      11  45451025  23944352.0   
614       sgsapp  20200906  total  total_total      11  45672367  24181362.0   
638       sgsapp  20200907  total  total_total      11  45891409  22423886.0   
662       sgsapp  20200908  total  total_total      11  46110247  22924422.0   
686       sgsapp  20200909  total  total_total      11  46332643  23939396.0   
710       sgsapp  20200910  total  total_total      11  46558855  24049218.0   

     dis_user  refresh_times   real_dis  ...       ctr  real_ctr  read_ratio  \
11   326204.0      1542618.0  7551142.0  ...  0.077666  0.268186    0.341964   
35   327458.0      1547216.0  7532744.0  ...  0.080672  0.281502    0.342377   
59   324022.0      1541032.0  7452292.0  ...  0.078436  0.274347    0.325768   
83   323166.0      1524262.0  7452940.0  ...  0.077736  0.267924    0.322819   
107  323712.0      1531932.0  7515742.0  ...  0.080455  0.277457    0.323707   
131  323308.0      1528226.0  7597820.0  ...  0.082049  0.281191    0.329123   
155  322996.0      1503052.0  7199748.0  ...  0.085980  0.301874    0.322004   
179  325310.0      1492756.0  7163166.0  ...  0.091183  0.319862    0.324140   
203  325558.0      1516802.0  7201298.0  ...  0.089749  0.317130    0.323045   
227  326676.0      1537610.0  7253824.0  ...  0.087115  0.308033    0.320544   
251  324700.0      1518598.0  7086024.0  ...  0.087674  0.312458    0.315023   
275  322456.0      1492306.0  7087876.0  ...  0.089807  0.316303    0.316849   
299  325508.0      1520108.0  7268932.0  ...  0.091828  0.321596    0.315329   
323  322770.0      1496466.0  7093024.0  ...  0.088442  0.310995    0.314930   
347  315354.0      1476656.0  6888064.0  ...  0.086193  0.305883    0.312715   
371  320948.0      1523558.0  7166750.0  ...  0.090150  0.319868    0.320083   
393  322240.0      1507130.0  7118118.0  ...  0.093791  0.333001    0.324460   
409

In [15]:
w.base[w.base.name=='video'][w.base.data_obj=='total_total']

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



product_name      date   name     data_obj  abtest          id  \
23        sgsapp  20200811  video  total_total     5.0  39991579.0   
47        sgsapp  20200812  video  total_total     5.0  40160617.0   
71        sgsapp  20200813  video  total_total     5.0  40329579.0   
95        sgsapp  20200814  video  total_total     5.0  40498035.0   
119       sgsapp  20200815  video  total_total     5.0  40668063.0   
143       sgsapp  20200816  video  total_total     5.0  40838371.0   
167       sgsapp  20200817  video  total_total     5.0  41009219.0   
191       sgsapp  20200818  video  total_total     5.0  41179195.0   
215       sgsapp  20200819  video  total_total     5.0  41348853.0   
239       sgsapp  20200820  video  total_total     5.0  41520009.0   
263       sgsapp  20200821  video  total_total     5.0  41693067.0   
287       sgsapp  20200822  video  total_total     5.0  41867009.0   
311       sgsapp  20200823  video  total_total     5.0  42040381.0   
335       sgsapp  20200824  video  total_total     5.0  42952761.0   
359       sgsapp  20200825  video  total_total     5.0  43172523.0   
383       sgsapp  20200826  video  total_total     5.0  43391553.0   
401       sgsapp  20200827  video  total_total     5.0  43599457.0   
437       sgsapp  20200829  video  total_total     5.0  43914243.0   
458       sgsapp  20200830  video  total_total     5.0  44128489.0   
482       sgsapp  20200831  video  total_total     5.0  44340769.0   
506       sgsapp  20200901  video  total_total     5.0  44562329.0   
530       sgsapp  20200902  video  total_total     5.0  44784007.0   
554       sgsapp  20200903  video  total_total     5.0  45005935.0   
578       sgsapp  20200904  video  total_total     5.0  45227715.0   
602       sgsapp  20200905  video  total_total     5.0  45450655.0   
626       sgsapp  20200906  video  total_total     5.0  45671997.0   
650       sgsapp  20200907  video  total_total     5.0  45891027.0   
674       sgsapp  20200908  video  total_total     5.0  46109835.0   
698       sgsapp  20200909  video  total_total     5.0  46332237.0   
722       sgsapp  20200910  video  total_total     5.0  46558443.0   

              dis       dis_user  refresh_times      real_dis  ...       ctr  \
23   1.183794e+07  319213.333333  739710.000000  2.562957e+06  ...  0.145873   
47   1.214168e+07  321802.000000  726163.333333  2.585904e+06  ...  0.149378   
71   1.174525e+07  316985.333333  737519.333333  2.518512e+06  ...  0.145622   
95   1.164839e+07  317555.333333  730128.666667  2.544996e+06  ...  0.145215   
119  1.170609e+07  318074.000000  696788.000000  2.541371e+06  ...  0.149617   
143  1.198495e+07  317580.000000  692847.333333  2.586839e+06  ...  0.152501   
167  1.176718e+07  316364.666667  737353.333333  2.544873e+06  ...  0.147668   
191  1.177825e+07  318883.333333  716776.666667  2.565162e+06  ...  0.146748   
215  1.188949e+07  319610.000000  742062.666667  2.567743e+06  ...  0.145473   
239  1.187519e+07  320382.000000  766280.666667  2.593088e+06  ...  0.142223   
263  1.158596e+07  318517.333333  709908.666667  2.499843e+06  ...  0.140343   
287  1.161645e+07  316638.000000  706416.000000  2.513078e+06  ...  0.142951   
311  1.192107e+07  318357.333333  761600.000000  2.615359e+06  ...  0.148106   
335  1.159355e+07  316711.333333  777900.666667  2.584246e+06  ...  0.141965   
359  1.122877e+07  308698.000000  732140.666667  2.486333e+06  ...  0.141660   
383  1.177772e+07  314043.333333  776640.666667  2.574029e+06  ...  0.149607   
401  1.179896e+07  315946.000000  802348.000000  2.608764e+06  ...  0.151320   
437  1.193355e+07  313578.666667  761451.333333  2.599943e+06  ...  0.155391   
458  1.185967e+07  312773.333333  744563.333333  2.588424e+06  ...  0.157911   
482  1.102495e+07  299855.333333  702124.000000  2.401407e+06  ...  0.149494   
506  1.028502e+07  288504.000000  644037.333333  2.266994e+06  ...  0.143700   
530  1.041097e+07  286004.666667  688424.666667  2.297555e+06  ...  0.141

In [16]:
show_daily('total_total_total')

In [17]:
show_daily('total_quality_total')

In [18]:
show_daily('total_quality_total')

In [19]:
show_daily('tuwen_quality_total')

In [20]:
show_daily('video_total_recommend')

In [21]:
show_daily('video_quality_relative')

refresh_times with same vals ignore


In [22]:
show_daily('tuwen_total_total')

In [23]:
w.ratio

product_name      date         name           data_obj  abtest        id  \
0         sgsapp  20200811  small_video  quality_recommend      11 -0.000003   
1         sgsapp  20200811  small_video   quality_relative      11 -0.000003   
2         sgsapp  20200811  small_video      quality_total      11 -0.000003   
3         sgsapp  20200811  small_video    total_recommend      11 -0.000003   
4         sgsapp  20200811  small_video     total_relative      11 -0.000003   
..           ...       ...          ...                ...     ...       ...   
718       sgsapp  20200910        video   quality_relative      11 -0.000003   
719       sgsapp  20200910        video      quality_total      11 -0.000003   
720       sgsapp  20200910        video    total_recommend      11 -0.000003   
721       sgsapp  20200910        video     total_relative      11 -0.000003   
722       sgsapp  20200910        video        total_total      11 -0.000003   

          dis  dis_user  refresh_times  real_dis  ...       ctr  real_ctr  \
0   -0.025541 -0.023782      -0.700000 -0.103734  ... -0.234176 -0.150510   
1    0.605559  0.054945       0.000000  0.000000  ...  0.502255  1.342525   
2   -0.002959 -0.009729       0.000517 -0.134228  ...  1.180379  1.370195   
3    0.006820  0.007116      -0.035714 -0.049566  ... -0.482927 -0.451853   
4   -0.018132  0.020528       0.000000  0.000000  ... -0.105700 -0.125978   
..        ...       ...            ...       ...  ...       ...       ...   
718  0.007061  0.012851       0.000000  0.000000  ... -0.003697  0.003337   
719  0.009736  0.012922       0.004155  0.020675  ... -0.003588 -0.014356   
720  0.015913  0.008818       0.008839  0.026326  ... -0.000868 -0.011007   
721  0.010469  0.011319       0.000000 -0.009634  ... -0.012849  0.005962   
722  0.012542  0.008369       0.006764  0.023823  ... -0.011643 -0.022551   

     read_ratio      dur1      dur2  finish_ratio  read_files   doc_dur  \
0     -0.160345  0.564084  1.016101     -0.073529   -0.241443  1.148586   
1      0.297069  1.901776  1.265319     -0.122285    1.193677  0.249487   
2      0.346615  1.458339  0.811266     -0.219364    1.187039  0.112988   
3     -0.419055 -0.391698  0.043374     -0.078557   -0.483204  0.175498   
4      0.042932 -0.260831 -0.291324     -0.165437   -0.139142 -0.135529   
..          ...       ...       ...           ...         ...       ...   
718    0.006896  0.033857  0.026814     -0.081539   -0.009396  0.043632   
719    0.005270  0.031664  0.026305     -0.081701   -0.006730  0.038664   
720   -0.001268  0.046276  0.047651     -0.019338    0.006141  0.040000   
721    0.005513  0.039623  0.034000     -0.083902   -0.013725  0.054122   
722    0.000755  0.043101  0.042347     -0.082245   -0.007571  0.051121   

      refresh  refresh2  
0   -0.692344 -0.583127  
1   -0.062880 -0.279548  
2    0.011076 -0.253030  
3   -0.047166  0.664313  
4   -0.023310 -0.063514  
..        ...       ...  
718 -0.012689 -0.019532  
719 -0.008656 -0.013904  
720  0.000016  0.001285  
721 -0.011200 -0.016637  
722 -0.001595 -0.002352  

[723 rows x 33 columns]